## Ingesting Book....

In [3]:
from pathlib import Path
from bs4 import BeautifulSoup
from langchain.schema import Document
import re
import nltk

# Télécharger le tokenizer de phrase si nécessaire
nltk.download('punkt')
from nltk.tokenize import sent_tokenize

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\noeay\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [6]:


class HTMLLoader:
    """
    Loader HTML avancé : 
    - extrait les phrases des <p>
    - gère pages implicites et ranges
    - regroupe phrases courtes
    """

    # numéros entre parenthèses 1 à 3 chiffres (exclut les années)
    PAGE_PATTERN = re.compile(r'\((\d{1,3})(?!\d)\)')

    def __init__(self, folder_path: str, min_sent_len=50):
        self.folder = Path(folder_path)
        self.min_sent_len = min_sent_len

    def _split_sentences_with_pages(self, text: str, last_page=None):
        sentences = sent_tokenize(text, language='french')
        result = []

        # parcourir toutes les phrases et assigner la page
        for i, sentence in enumerate(sentences):
            pages_in_sentence = self.PAGE_PATTERN.findall(sentence)
            if pages_in_sentence:
                x = int(pages_in_sentence[-1]) + 1 
                page = f"{last_page}-{x}" if last_page else str(x)
                last_page = x
            else:
                page = str(last_page) if last_page else "unknown"

            # si page unknown, chercher la prochaine page dans le reste
            if page == "unknown":
                for future_sentence in sentences[i+1:]:
                    match = self.PAGE_PATTERN.search(future_sentence)
                    if match:
                        page = match.group(1)
                        break
                if page == "unknown":
                    page = str(last_page) if last_page else "unknown"

            result.append((sentence, page))

        return result, last_page

    def _group_short_sentences(self, sentences_with_pages):
        grouped = []
        buffer = []
        buffer_page = None

        for sentence, page in sentences_with_pages:
            if not buffer:
                buffer.append(sentence)
                buffer_page = page
            elif len(sentence) < self.min_sent_len and page == buffer_page:
                buffer.append(sentence)
            else:
                grouped.append((" ".join(buffer), buffer_page))
                buffer = [sentence]
                buffer_page = page
        if buffer:
            grouped.append((" ".join(buffer), buffer_page))
        return grouped

    def load(self):
        documents = []
        for html_file in self.folder.glob("*.html"):
            soup = BeautifulSoup(html_file.read_text(encoding="utf-8"), "html.parser")
            paragraphs = soup.find_all("p")
            last_page = None
            for p in paragraphs:
                text = p.get_text().strip()
                if not text:
                    continue
                sentences_with_pages, last_page = self._split_sentences_with_pages(text, last_page)
                grouped_sentences = self._group_short_sentences(sentences_with_pages)
                for sentence, page in grouped_sentences:
                    documents.append(Document(
                        page_content=sentence,
                        metadata={"book": html_file.name, "page": page}
                    ))
        return documents


In [7]:
loader = HTMLLoader("data")
docs = loader.load()
print(f"{len(docs)} phrases chargées et prêtes pour vectorisation.")

11319 phrases chargées et prêtes pour vectorisation.


## Vector Embeddings

In [41]:
!ollama list
# # Pull sfr-embedding-mistral model from Ollama if you don't have it
#!ollama pull sfr-embedding-mistral

NAME                                ID              SIZE      MODIFIED      
avr/sfr-embedding-mistral:latest    3a707fec6ecc    4.4 GB    4 minutes ago    
qwen3:latest                        500a1f067a9f    5.2 GB    5 weeks ago      
deepseek-r1:latest                  6995872bfe4c    5.2 GB    2 months ago     
qwen2:0.5b                          6f48b936a09f    352 MB    3 months ago     
llama3.2:3b                         a80c4f17acd5    2.0 GB    4 months ago     
llama3.2:latest                     a80c4f17acd5    2.0 GB    6 months ago     
mistral:latest                      f974a74358d6    4.1 GB    6 months ago     
qwen2.5:latest                      845dbda0ea48    4.7 GB    6 months ago     
mxbai-embed-large:latest            468836162de7    669 MB    6 months ago     
deepseek-r1:1.5b                    a42b25d8c10a    1.1 GB    6 months ago     


In [4]:
from langchain_ollama import OllamaEmbeddings
from langchain_community.vectorstores import Chroma


model_name = "avr/sfr-embedding-mistral"
vector_db = Chroma(persist_directory= "./book_db",embedding_function= OllamaEmbeddings(model=model_name),collection_name="raw_book")

C:\Users\noeay\AppData\Local\Temp\ipykernel_5384\768469752.py:6: LangChainDeprecationWarning: The class `Chroma` was deprecated in LangChain 0.2.9 and will be removed in 1.0. An updated version of the class exists in the :class:`~langchain-chroma package and should be used instead. To use it run `pip install -U :class:`~langchain-chroma` and import as `from :class:`~langchain_chroma import Chroma``.
  vector_db = Chroma(persist_directory= "./book_db",embedding_function= OllamaEmbeddings(model=model_name),collection_name="raw_book")


In [ ]:
from tqdm import tqdm

#for document in tqdm(docs, desc="Calcul des embeddings"):
#    try:
#        vector_db.add_documents([document])
#    except: 
#        print("Error on : ", document)
        
#vector_db.persist()

Calcul des embeddings: 100%|██████████| 11319/11319 [15:02<00:00, 12.54it/s]
C:\Users\noeay\AppData\Local\Temp\ipykernel_25784\2080410965.py:9: LangChainDeprecationWarning: Since Chroma 0.4.x the manual persistence method is no longer supported as docs are automatically persisted.
  vector_db.persist()


In [ ]:
import plotly.express as px
import pandas as pd
import numpy as np
from sklearn.manifold import TSNE

# Récupérer toutes les vecteurs et metadata depuis la collection
results = vector_db.get(include=["metadatas", "documents", "embeddings"])

# Embeddings
embeddings = [np.array(e, dtype=float) for e in results["embeddings"]]  # liste de listes de floats

# Metadata
metadata = results["metadatas"]     # liste de dicts
phrases = results["documents"]      # liste de chaînes
ids = results["ids"]


df = pd.DataFrame({
    "id" : ids,
    "embedding": embeddings,
    "book": [m['book'] for m in metadata],
    "page": [m.get('page', "") for m in metadata],
    "phrase": phrases
})

# t-SNE sur embeddings
tsne_result = TSNE(n_components=2, random_state=1).fit_transform(np.array(df['embedding'].to_list()))

df['x'] = tsne_result[:,0]
df['y'] = tsne_result[:,1]

# Plot interactif
fig = px.scatter(
    df,
    x="x",
    y="y",
    color="book",
    hover_data={"phrase": True, "page": True},
    title="Visualisation t-SNE des phrases vectorisées"
)

fig.show()


In [ ]:
#mask_to_remove = (df['x'].between(-56, -51)) & (df['y'].between(-80, -70))

#ids_to_delete = df.loc[mask_to_remove, "id"].tolist()

#print("À supprimer :", vector_db.get(ids=ids_to_delete)["documents"])

#vector_db.delete(ids=ids_to_delete)
#print(f"{len(ids_to_delete)} points supprimés du vector_db ✅")
#vector_db.persist()

## Regroupoement des citation en triplet

In [9]:
from collections import defaultdict

def build_triplets(vector_db, book_pivot="la-connaissance-de-la-vie-de-georges-canguilhem.html", k=20):
    # Récupère tous les embeddings et IDs du pivot
    results = vector_db.get(where={"book": book_pivot}, include=["embeddings", "metadatas", "documents"])
    pivot_embeddings = results["embeddings"]
    pivot_ids = results["ids"]
    pivot_meta = results["metadatas"]

    # Récupère tous les documents et IDs pour mapping texte -> ID
    all_docs = vector_db.get(include=["documents"])
    doc_to_id = {doc: id_ for doc, id_ in zip(all_docs["documents"], all_docs["ids"])}

    triplets = []

    for pid, pvec, pmeta in zip(pivot_ids, pivot_embeddings, pivot_meta):
        # Cherche proches voisins
        neighbors = vector_db.similarity_search_by_vector(pvec, k=k)
        
        # Filtre pour exclure le livre pivot
        neighbors = [n for n in neighbors if n.metadata.get("book") != book_pivot]

        # Regroupe par livre
        by_book = defaultdict(list)
        for n in neighbors:
            by_book[n.metadata.get("book")].append(n)

        # Création des triplets ou doublets
        if len(by_book) >= 2:
            books = list(by_book.keys())[:2]  # 2 livres différents
            n1, n2 = by_book[books[0]][0], by_book[books[1]][0]
            for n1 in by_book[books[0]] :
                for n2 in by_book[books[1]] :
                    id1, id2 = doc_to_id[n1.page_content], doc_to_id[n2.page_content]
                    triplets.append((pid, id1, id2))

    return triplets

triplets = build_triplets(vector_db, k=20)

for (a,b,c) in triplets:
    try:
        print(vector_db.get(ids = [a,b,c])["documents"])
    except:
        print("hum")


['La connaissance', 'Extraits et citations, sur le thème de «\xa0Expériences de la nature\xa0»', 'J’appris au Canadien et à Conseil le résultat de mes observations. Ned voulait savoir où allait le Nautilus. Peut-être le capitaine']
['La connaissance', 'Extraits et citations, sur le thème de «\xa0Expériences de la nature\xa0»', 'Résumé et recueil de citations sur le thème de «\xa0Expériences de la nature\xa0»']
['La connaissance', 'Extraits et citations, sur le thème de «\xa0Expériences de la nature\xa0»', 'Texte intégral']
['de la vie', 'Extraits et citations, sur le thème de «\xa0Expériences de la nature\xa0»', 'Résumé et recueil de citations sur le thème de «\xa0Expériences de la nature\xa0»']
['de la vie', 'Extraits et citations, sur le thème de «\xa0Expériences de la nature\xa0»', 'Texte intégral']
['de la vie', 'Extraits et citations, sur le thème de «\xa0Expériences de la nature\xa0»', 'établis par Bernard Martial, ex-professeur de lettres en CPGE']
['de la vie', 'Extraits et cit

## Contextualisation 

In [ ]:
from langchain_ollama.llms import OllamaLLM
from langchain.prompts import PromptTemplate
from langchain.schema import Document
from pathlib import Path
from bs4 import BeautifulSoup

# 1️⃣ Instancie le modèle Ollama
llm = OllamaLLM(model="mistral", temperature=0.0, max_tokens=200)

# 2️⃣ Prépare le prompt template (même logique que le prompt direct)
templateCTX = """
Tu es un contextualiseur FR pour dissertation sur le thème de l'expérience et de la nature.
On y aborde des sujets sur la science, la raison, le language et les relations animal-humain / nature-humain.

Entrées :
- CITATION : "{citation}"
- PARAGRAPHE_SOURCE : "{paragraph}"
- METADATA : book="{book}", page="{page}"

Consignes :
1) Si la CITATION est du bruit (notes, titres, numéros, symboles, texte illisible ou hors propos), réponds exactement : null

2) Sinon, produis uniquement l’une des deux formes suivantes (jamais plus) :
   - Forme 1 : Attribution contrôlée
       * Si un locuteur identifiable est mentionné => <locuteur> <verbe_approprié> : « CITATION » (p. <page>).
         - Choisir un verbe adapté :
             - question → "questionne"
             - exclamation → "s’exclame"
             - réplique → "répond"
             - affirmation → "déclare"
       * Si aucun locuteur n’est donné => Dans le livre ..., on lit : « CITATION » (p. <page>).

   - Forme 2 (facultative, max 25 mots) : Une seule phrase de contextualisation, utile dans une dissertation.

3) Ne fournis aucune explication, justification ni métadonnée en sortie.
4) La réponse doit être uniquement "null" ou le texte final demandé.

---

Exemple :

Entrées :
- CITATION : "De ce que certains hommes se sont voués à vivre pour savoir faut-il croire que l’homme ne vit vraiment que dans la science et par elle ?"
- PARAGRAPHE_SOURCE : "..."
- METADATA : book="la-connaissance-de-la-vie-de-georges-canguilhem.html", page="12"

Sortie attendue :
Dans *La connaissance de la vie* de Georges Canguilhem (p. 12), l’auteur questionne la primauté de la science sur l’expérience vécue lorsqu’il écrit :
« De ce que certains hommes se sont voués à vivre pour savoir faut-il croire que l’homme ne vit vraiment que dans la science et par elle ? »
Cette interrogation met en lumière la tension entre le savoir scientifique et la jouissance immédiate de la vie.
"""

promptCTX = PromptTemplate(
    input_variables=["citation", "paragraph", "book", "page"],
    template=templateCTX
)


templateARES = """
Tu es un assistant de rédaction philosophique. 
Ta tâche est de produire **un unique paragraphe continu** de dissertation structuré selon ARES (Argument, Référence, Exemples, Synthèse) à partir de trois citations exactes.

### Contraintes :
- Argument : phrase affirmative, construite à partir de la citation A.
- Référence : citation exacte A, qui appuie l’argument.
- Exemples : citations exactes B et C illustrant l’argument avec des situations concrètes.
- Synthèse : phrase finale rappelant l’argument et reliant les exemples.
- Écrire en français académique, style dissertation.
- Commencer le paragraphe par une tabulation.
- Terminer le paragraphe par un retour à la ligne.

### Exemple d’entrée :
ref_a : "Connaître c’est analyser."
ex_b  : "Celle-là, que puis-je comprendre à son comportement."
ex_c  : "Mais d’observer, d’étudier, de classer, il n’était plus question alors."

### Exemple de sortie attendue :

	Le savoir doit être orienté vers la compréhension de ses propres opérations, et non seulement vers une finalité extérieure. Dans *La connaissance de la vie* de Georges Canguilhem (p. unknown), on lit : "Connaître c’est analyser." L'auteur répond à ce problème par une affirmation de suffisance et de pureté du savoir, mais il admet que le savoir doit avoir un sens et refuse de lui trouver un autre sens que lui-même. Cette déclaration souligne la nécessité d'une attention accrue aux opérations du connaître pour comprendre le sens du connaître. Dans *Le Mur invisible* de Marlen Haushofer (p. 126), on lit : "Celle-là, que puis-je comprendre à son comportement." La chatte est un animal mystérieux et difficile à atteindre pour l'humain, illustrant la difficulté de comprendre un phénomène sans observation attentive. Dans *Vingt mille lieues sous les mers* de Jules Verne (p. 585), on lit : "Mais d’observer, d’étudier, de classer, il n’était plus question alors." Cette phrase souligne la dévotion du capitaine Nemo à l'étude et à l'observation des créatures marines, démontrant l'importance de focaliser le savoir sur l'objet étudié. Ces exemples montrent que l’analyse et l’attention aux opérations du savoir sont essentielles pour comprendre le réel, confirmant que la connaissance doit être orientée vers elle-même et non vers une finalité extérieure.

### Entrées :
- Citation de référence (A) : {ref_a}
- Exemple 1 (B) : {ex_b}
- Exemple 2 (C) : {ex_c}

### Sortie :
Génère uniquement un **paragraphe continu** intégrant l’argument, la référence et les exemples B et C, puis la synthèse finale.
"""


promptARES = PromptTemplate(
    input_variables=["ref_a", "ex_b", "ex_c"],
    template=templateARES
)



def get_paragraph_for_quote(doc : Document) -> str | None:
    """
    Extrait le paragraphe <p> contenant la citation dans un fichier HTML.
    Si le paragraphe exact n'est pas trouvé, tente une correspondance partielle.
    
    Args:
        html_path (str): chemin vers le fichier HTML
        quote (str): texte exact ou partiel de la citation
    
    Returns:
        str | None: le texte du paragraphe ou None si non trouvé
    """
    html_file = Path("./data/"+doc.metadata["book"])
    if not html_file.exists():
        return None
    
    soup = BeautifulSoup(html_file.read_text(encoding="utf-8"), "html.parser")
    
    for p in soup.find_all("p"):
        text = p.get_text(separator=" ", strip=True)
        if doc.page_content in text:
            return text
    
    return None

# 3️⃣ Fonction pratique pour générer la phrase contextualisée
def contextualize_langchain(doc : Document):
    out = llm(promptCTX.format(
        citation=doc.page_content,
        paragraph=get_paragraph_for_quote(doc),
        book=doc.metadata["book"],
        page=doc.metadata["page"]
    ))
    # retour None si null
    #if out.strip().lower() == "null":
    #    return None
    return out.strip()



def construire_ares(a, b, c, vector_db):
    """
    Construit un paragraphe de dissertation ARES à partir de 3 ids Chroma.
    
    Args:
        a, b, c (str): ids internes Chroma (a = référence, b et c = exemples)
        vector_db: instance Chroma ou équivalent
    
    Returns:
        str | None: le paragraphe ARES généré ou None si contextualisation impossible
    """
    # 1️⃣ Récupérer les documents depuis la base
    docs = vector_db.get(ids=[a, b, c], include=["documents", "metadatas"])
    if not docs or "documents" not in docs:
        return None
    
    # Transformation en objets Document
    documents = []
    for content, meta in zip(docs["documents"], docs["metadatas"]):
        documents.append(Document(page_content=content, metadata=meta))
    
    if len(documents) != 3:
        return None

    doc_a, doc_b, doc_c = documents

    # 2️⃣ Contextualiser chaque citation
    ref_a = contextualize_langchain(doc_a)
    #print("ref A : "+ref_a)
    ex_b  = contextualize_langchain(doc_b)
    #print("ex B : "+ex_b)
    ex_c  = contextualize_langchain(doc_c)
    #print("ex C : "+ex_c)

    # Vérifie si une contextualisation est nulle → inutile de continuer
    if any(x.lower() == "null" for x in [ref_a, ex_b, ex_c]):
        return None

    # 3️⃣ Générer le paragraphe ARES
    paragraphe = llm(promptARES.format(
        ref_a=ref_a,
        ex_b=ex_b,
        ex_c=ex_c
    ))

    return paragraphe.strip()


In [13]:
(a,b,c) = triplets[50]
print(vector_db.get(ids = [a,b,c])["documents"])

para = construire_ares(a, b, c, vector_db)
print("\n\noutput: "+para)

['Connaître c’est analyser.', 'Celle-là, que puis-je comprendre à son comportement.', 'Mais d’observer, d’étudier, de classer, il n’était plus question alors.']
ref A : Dans *La connaissance de la vie* de Georges Canguilhem (p. unknown), on lit : "Connaître c’est analyser." L'auteur répond à ce problème par une affirmation de suffisance et de pureté du savoir, mais il souligne que savoir pour savoir ce n'est guère plus sensé que manger pour manger ou tuer pour tuer ou rire pour rire, puisque c'est à la fois l’aveu que le savoir doit avoir un sens et le refus de lui trouver un autre sens que lui-même. Cette affirmation met en lumière la tension entre le savoir scientifique et sa signification réelle.
ex B : Dans *Le Mur invisible* de Marlen Haushofer (p. 126), on lit : "Celle-là, que puis-je comprendre à son comportement."
   La chatte est un animal mystérieux et difficile à atteindre pour l'humain.
ex C : Dans *Vingt mille lieues sous les mers* de Jules Verne (p. 585), on lit : "Mais d

In [1]:
import json
#from tqdm import tqdm

# 1️⃣ Générer et sauvegarder tous les paragraphes
results = []

#for (a, b, c) in tqdm(triplets, desc="Génération ARES"):
#    try:
#        para = construire_ares(a, b, c, vector_db)
#        if para:
#            results.append({
#                "ids": [a, b, c],
#                "paragraph": para
#            })
#    except:
#        print("humm")


# Sauvegarde dans un fichier JSON
#output_file = "data/ares_paragraphs.json"
#with open(output_file, "w", encoding="utf-8") as f:
#    json.dump(results, f, ensure_ascii=False, indent=2)

#print(f"✅ {len(results)} paragraphes ARES sauvegardés dans {output_file}")

with open("data/ares_paragraphs.json", "r", encoding="utf-8") as f:
    results = json.load(f)


In [ ]:
vector_ARES_db = Chroma(persist_directory= "./ares_db",embedding_function= OllamaEmbeddings(model=model_name),collection_name="ARES_list")

#from tqdm import tqdm

#for ares in tqdm(results, desc="Calcul des embeddings"):
#    try:
#        vector_ARES_db.add_documents([Document(ares["paragraph"],metadata= {"ref_id":ares["ids"][0], "ex_a_id":ares["ids"][1],"ex_b_id":ares["ids"][2]})])
#    except: 
#        print("Error on : ", ares["paragraph"])
        
#vector_ARES_db.persist()

Calcul des embeddings: 100%|██████████| 3115/3115 [14:09<00:00,  3.67it/s]
C:\Users\noeay\AppData\Local\Temp\ipykernel_5384\249415234.py:11: LangChainDeprecationWarning: Since Chroma 0.4.x the manual persistence method is no longer supported as docs are automatically persisted.
  vector_ARES_db.persist()


In [13]:
len(results["ids"])

3115

In [15]:
import plotly.express as px
import pandas as pd
import numpy as np
from sklearn.manifold import TSNE

def get_first_sentence(text):
    sentences = sent_tokenize(text.strip())
    return sentences[0] if sentences else text

# Récupérer toutes les vecteurs et metadata depuis la collection
results = vector_ARES_db.get(include=["metadatas", "documents", "embeddings"])

# Embeddings
embeddings = [np.array(e, dtype=float) for e in results["embeddings"]]  # liste de vecteurs numpy

# Metadata et infos
metadata = results["metadatas"]  # liste de dicts
phrases = results["documents"]   # liste de paragraphes
ids = results["ids"]

# Construire DataFrame
df = pd.DataFrame({
    "id": ids,
    "embedding": embeddings,
    "ref_id": [m.get("ref_id", "") for m in metadata],
    "ex_a_id": [m.get("ex_a_id", "") for m in metadata],
    "ex_b_id": [m.get("ex_b_id", "") for m in metadata],
    "paragraph": [get_first_sentence(ph) for ph in phrases]
})

# t-SNE sur embeddings
tsne_result = TSNE(n_components=2, random_state=1).fit_transform(np.array(df['embedding'].to_list()))

df['x'] = tsne_result[:, 0]
df['y'] = tsne_result[:, 1]

# Plot interactif avec hover personnalisé
fig = px.scatter(
    df,
    x="x",
    y="y",
    color="ref_id",  # Colorisation par ref_id
    hover_data={
        "id": True,
        "paragraph": True,
        "ref_id": True,
        "ex_a_id": True,
        "ex_b_id": True,
        "x": False, "y": False  # pas besoin d'afficher les coordonnées dans le hover
    },
    title="Visualisation t-SNE des ARES (colorisés par ref_id)"
)

fig.show()


# Introduction 

amorce 

sujet 

analyse

problematique 

plan

In [61]:
from langchain_ollama.llms import OllamaLLM
from langchain.prompts import PromptTemplate
from bs4 import BeautifulSoup
import requests

def analyse_semantique_complete(citation: str, model_name="mistral") -> str:
    """
    Analyse une citation et génère un ou deux paragraphes reformulés en utilisant
    les définitions des mots clés extraits pour une dissertation.
    
    Args:
        citation (str): texte exact de la citation
        model_name (str): nom du modèle Ollama à utiliser
    
    Returns:
        str: reformulations sémantiques de la citation
    """
    # 1️⃣ Instancie le LLM
    llm = OllamaLLM(model=model_name, temperature=0.0, max_tokens=400)
    
    # 2️⃣ Fonction interne : extraire les mots clés via le LLM
    def extract_keywords(text: str):
        template = """Texte :
"{text}"

Tâche :
- Extrait uniquement les mots clés (concepts centraux, notions importantes).
- Retourne la liste sous forme de mots séparés par des virgules, sans explications.
"""
        prompt = PromptTemplate(input_variables=["text"], template=template)
        formatted_prompt = prompt.format(text=text)
        response = llm(formatted_prompt)
        keywords_raw = response.strip().lower()
        return [k.strip() for k in keywords_raw.split(",") if k.strip()]
    
    # 3️⃣ Fonction interne : récupérer définitions CNRTL
    def fetch_definitions_cnrtl(word: str) -> list[str]:
        url = f"https://www.cnrtl.fr/definition/{word}"
        try:
            r = requests.get(url, timeout=5)
            r.raise_for_status()
            soup = BeautifulSoup(r.text, "html.parser")
            defs = [li.get_text(separator=" ", strip=True) for li in soup.select("li, div.def")]
            return defs[:3]  # limiter à 3 définitions
        except:
            return []

    # 4️⃣ Extraire mots clés
    keywords = extract_keywords(citation)

    # 5️⃣ Chercher définitions pour chaque mot clé
    keywords_defs = {}
    for kw in keywords:
        defs = fetch_definitions_cnrtl(kw)
        if defs:
            keywords_defs[kw] = defs

    defs_text = "\n".join([f"{k} : {', '.join(v)}" for k, v in keywords_defs.items()]) \
                if keywords_defs else "Aucune définition trouvée."
    
    # 6️⃣ Template pour reformuler la citation
    semantic_template =  PromptTemplate(
    input_variables=["citation", "keywords_defs"],
    template="""
Tu es un assistant philosophique et linguistique en français.
Tâche :
- Prends la citation suivante et les mots clés avec leurs définitions.
- Rédige **un paragraphe fluide et académique** en français qui :
  1. Explique les mots clés par leurs définitions.
  2. Reformule la citation en intégrant ces définitions.
  3. Si plusieurs définitions sont possibles, souligne la dualité et propose une reformulation intégrant les sens multiples.
- Ne fais pas de liste, numérotation, ou tirets. Le texte doit être un **unique paragraphe cohérent**.

Exemple :

Citation :
"Connaître c’est analyser."

Mots clés et définitions :
Connaître : avoir la compréhension ou la connaissance de quelque chose
Analyser : examiner en détail pour comprendre ou expliquer

Paragraphe rédigé :
Par définition, connaître consiste à acquérir la compréhension ou la connaissance des phénomènes, tandis qu’analyser implique un examen minutieux pour en expliciter les mécanismes. On peut donc reformuler la citation comme suit : la connaissance véritable passe par une analyse attentive des objets étudiés, car comprendre implique de décomposer et d’interpréter leurs éléments constitutifs. Si l’on considère qu’« analyser » peut aussi signifier interpréter ou critiquer, alors la citation prend une dimension double : connaître c’est à la fois comprendre et critiquer, mettant en évidence la richesse et la complexité du savoir.

---

Citation :
"{citation}"

Mots clés et définitions :
{keywords_defs}

Rédige maintenant **un paragraphe unique** en français suivant la même logique que l’exemple ci-dessus.
"""
)
    
    prompt_text = semantic_template.format(citation=citation, keywords_defs=defs_text)
    
    # 7️⃣ Lancer le LLM
    output = llm(prompt_text)
    return output.strip()


from langchain_ollama.llms import OllamaLLM
from langchain.prompts import PromptTemplate



def analyse_stylistique(citation: str, model_name="mistral") -> str:
    """
    Analyse stylistiquement une citation et renvoie un paragraphe rédigé.

    Args:
        citation (str): La citation à analyser

    Returns:
        str: Paragraphe unique analysant les procédés stylistiques et leurs effets
    """
    # Instancie le modèle Ollama
    llm = OllamaLLM(model=model_name, temperature=0.0, max_tokens=300)

    # Template stylistique
    style_template = PromptTemplate(
        input_variables=["citation"],
        template="""
Tu es un analyste stylistique expert en français.
Tâche :
- Analyse la citation suivante uniquement sur le plan **littéraire et grammatical**.
- Identifie tous les procédés stylistiques et grammaticaux présents (ex : négation restrictive, temps verbaux, figures de style, structure syntaxique, répétitions, ellipse, hyperbole…).
- Pour chaque procédé, explique brièvement son effet sur le rythme, la tonalité, ou l’impact formel.
- Intègre ces observations dans un **paragraphe unique**, fluide, académique.
- Ne traite pas du sens ou de la sémantique générale.
- Commence le paragraphe par une tabulation et termine par un retour à la ligne.

Exemple :

Citation :
"Connaître c’est analyser."

Paragraphe rédigé :
	La phrase "Connaître c’est analyser" utilise une structure elliptique, condensant deux actions fondamentales en une formule brève, ce qui crée un rythme incisif et accentue la force de l’énoncé. L’infinitif confère une universalité intemporelle, tandis que la juxtaposition des deux verbes met en valeur leur corrélation. L’absence de sujet explicite et la concision du syntagme donnent un effet d’assertion forte et didactique.

Citation :
"{citation}"

Rédige maintenant un **paragraphe unique en français** analysant uniquement les procédés stylistiques et grammaticaux.
"""
    )
    prompt = style_template.format(citation=citation)
    resultat = llm(prompt)
    return resultat.strip()

def analyse_complete_llm(citation: str, model_name="mistral") -> str:
    """
    Génère une analyse complète de la citation en 3 paragraphes (sémantique, stylistique, problématique)
    """
    llm = OllamaLLM(model=model_name, temperature=0.0, max_tokens=500)
    template_analyse =  """
Tu es un assistant expert en dissertation philosophique.

Entrées :
- CITATION : "{citation}"
- ANALYSE_STYLISTIQUE : "{analyse_stylistique}"
- ANALYSE_SEMANTIQUE : "{analyse_semantique}"

Instructions :
1) Produis **trois paragraphes consécutifs**, chacun commençant par une tabulation et séparés par un simple retour à la ligne.
2) Premier paragraphe : analyse sémantique
   - Contient une reformulation de la citation intégrant les définitions pertinentes des mots-clés.
   - Ne répète pas l’analyse stylistique.
   - Rédige en français correct et académique.
3) Deuxième paragraphe : analyse stylistique
   - Analyse uniquement les procédés littéraires et grammaticaux.
   - Ne répète pas l’analyse sémantique.
   - Évite tout anglicisme ou expression inappropriée.
4) Troisième paragraphe : synthèse + problématique
   - Résume le thème et le sens mis en évidence.
   - Formule une problématique finale, finissant par un point d’interrogation.
   - Ne répète pas les détails des deux premiers paragraphes.

Contraintes :
- Chaque paragraphe commence par une tabulation.
- Écriture en français académique, style dissertation.
- Texte continu, pas de liste, pas de tirets.
- La problématique doit découler des deux analyses précédentes.
- Aucun anglicisme n’est toléré ; privilégier un vocabulaire strictement français.

Exemple :

Entrées :
- CITATION : "Connaître, c’est analyser."
- ANALYSE_SEMANTIQUE : "La connaissance consiste en l’acquisition et la compréhension des informations ; l’analyse consiste en l’examen détaillé des éléments pour en comprendre le sens."
- ANALYSE_STYLISTIQUE : "La citation utilise une structure synthétique et affirmative, le verbe à l’infinitif crée un effet universel et général, l’emploi du présent de vérité générale renforce la portée intemporelle."

Sortie attendue :

\tPar définition, la connaissance consiste en l’acquisition et la compréhension des informations tandis que l’analyse consiste en l’examen détaillé des éléments pour en comprendre le sens. On peut donc reformuler la citation ainsi : comprendre véritablement implique de procéder à une analyse minutieuse des objets ou concepts étudiés, faisant de l’analyse une condition du savoir.

\tLa citation adopte une structure synthétique et affirmative ; le choix du verbe à l’infinitif confère un effet universel et général, tandis que l’emploi du présent de vérité générale renforce sa portée intemporelle, soulignant la nécessité de considérer la connaissance comme un processus actif.

\tAinsi, la citation met en évidence que l’acte de connaître ne peut se dissocier de l’analyse et de l’examen critique. Cela soulève la problématique suivante : dans quelle mesure la connaissance authentique dépend-elle de la capacité à analyser et comprendre en profondeur les phénomènes observés ?

Rédige maintenant le texte complet **en français académique** conformément aux instructions ci-dessus, sans aucun anglicisme, et en juxtaposant les paragraphes comme indiqué.
"""



    promptAnalyse = PromptTemplate(
        input_variables=["citation", "analyse_stylistique", "analyse_semantique"],
        template=template_analyse
    )
    formatted_prompt = promptAnalyse.format(citation=citation, analyse_stylistique= analyse_stylistique(citation,model_name=model_name),analyse_semantique = analyse_semantique_complete(citation,model_name=model_name))
    resultat = llm(formatted_prompt)
    return resultat.strip()


In [64]:
print(analyse_complete_llm("On ne commande la nature qu’en lui obéissant", model_name="qwen2.5"))

Par définition, la nature désigne le monde physique et biologique qui entoure les êtres vivants, tandis que commander implique de contrôler ou d'influencer un système ou une entité, ce qui peut être interprété comme l'exercice d'une autorité ou de la maîtrise. L'obéissance, quant à elle, signifie respecter et exécuter les ordres ou les directives reçues. On peut donc reformuler la citation originale en soulignant cette dualité : "On ne domine la nature qu'en l'accompagnant dans ses lois", car commander la nature suppose de la contrôler, mais obéir à ses règles implique d'accepter et de respecter son ordre intrinsèque. Cette reformulation met en lumière que le véritable maîtrise s'obtient non pas par l'imposition, mais par une harmonie avec les principes naturels qui régissent l'univers.

	La citation "On ne commande la nature qu'en lui obéissant" met en œuvre plusieurs procédés stylistiques et grammaticaux qui influencent son impact formel. Tout d'abord, l'utilisation de la négation re